# 『人を知る』人工知能講座<br/><span style="color: #00B0F0;">Session 3 言語メディア</span><br/><span style="background-color: #1F4E79; color: #FFFFFF;">4-4c</span> マルチモーダル機械翻訳 (Multimodal Machine Translation)
次に、マルチモーダル機械翻訳モデルについての演習を行います。
テキストと映像を入力系列、テキストを出力系列とすることで、マルチモーダル機械翻訳においてもエンコーダ・デコーダモデルを使用できます。

今回は [Fairseq MMT](https://arxiv.org/abs/2203.09173) の Transformer モデルを使用して、実際に日本語のテキストを英語に翻訳します。

### 1. データセット
[VISA: An Ambiguous Subtitles Dataset for Visual Scene-Aware Machine Translation](https://arxiv.org/abs/2201.08054) という論文で構築されたマルチモーダル機械翻訳データセットを使用します。
VISAは、映画やドラマから収集した4万文の日英対訳字幕と対応する映像からなるデータセットで す。VISAの特徴は、ほとんどの原言語字幕、つまり日本語字幕が曖昧であることです。

以下のセルを実行し、データの例を見てみましょう。

In [15]:
# 映像のディスプレイ
from IPython.display import Video
Video('/data/nlp/multimodal/mmt/data/VISA_video/video/polysemy_2404463_3.mp4', width=512, embed=True)

In [12]:
# 日本語字幕と英語字幕の表示
!head -n 1 /data/nlp/multimodal/mmt/fairseq_mmt_AI/data/opvi-ja-en/test.ja
!head -n 1 /data/nlp/multimodal/mmt/fairseq_mmt_AI/data/opvi-ja-en/test.en

放せ ！
Let me go !


### 2. 前処理

次に、映像からI3D特徴量を抽出します。I3D映像の特徴は、[Quo Vadis, Action Recognition? A New Model and the Kinetics Dataset](https://arxiv.org/abs/1705.07750)で提案されており、主に行動認識を行うために利用されています。具体的には、pre-training済みの[GlouonCV](https://cv.gluon.ai/build/examples_action_recognition/feat_custom.html)ツールを用いてI3D特徴量を抽出します。

In [16]:
# 環境変数の設定 (4-3b とは別のバージョンの Fairseq を用いるため)
import os
%env PYTHONPATH=":/usr/local/virtualenvs/fairseq-mmt/lib/python3.8/site-packages"
%env PATH=":/usr/local/virtualenvs/fairseq-mmt/bin:{os.getenv('PATH')}"

env: PYTHONPATH=":/usr/local/virtualenvs/fairseq-mmt/lib/python3.8/site-packages"
env: PATH=":/usr/local/virtualenvs/fairseq-mmt/bin:":/usr/local/virtualenvs/fairseq-mmt/bin:/root/.local/bin:/usr/local/bin:/usr/local/cuda/bin:/usr/local/sbin:/usr/bin:/usr/sbin:/bin:/sbin:/usr/local/nvidia/bin""


In [ ]:
need to install gluoncv==0.11.0, mxnet==1.9.1

In [17]:
# I3D特徴量を抽出する
!python /data/nlp/multimodal/mmt/gluon-cv/scripts/action-recognition/feat_extract.py \
  --data-list /data/nlp/multimodal/mmt/data/VISA_video --model i3d_resnet50_v1_kinetics400 \
  --save-dir /data/nlp/multimodal/mmt/data/VISA_i3d_feature --num-segments 32

Traceback (most recent call last):
  File "/data/nlp/multimodal/mmt/gluon-cv/scripts/action-recognition/feat_extract.py", line 11, in <module>
    import mxnet as mx
ModuleNotFoundError: No module named 'mxnet'


前処理の結果を確認しましょう。

In [ ]:
!head /data/nlp/fairseq/TED_st/en-ja/train_st.tsv

### 3. モデルの訓練
マルチモーダル機械翻訳モデルの訓練を行います。  

モデルとして4層のエンコーダと4層のデコーダからなる Transformer モデルを採用します。
このモデルは、selective attentionとgated fusion mechanismを用いて、テキスト特徴量と映像特徴量を組み合わせてつかいます。

モデルの訓練には時間がかかるので、ここでは訓練の様子を確認するだけとします。
プログラムを実行し、しばらく出力を確認したらプログラムを停止させてください。

In [ ]:
!fairseq-train data-bin/opvi.ja-en \
 --save-dir checkpoints/VISA-ja2en/i3d/i3d-mask0 \
 --distributed-world-size $gpu_num -s ja -t en \
 --arch image_multimodal_transformer_SA_top \
 --dropout 0.3 \
 --criterion label_smoothed_cross_entropy --label-smoothing 0.1 \
 --task image_mmt --image-feat-path /data/nlp/multimodal/mmt/data/VISA_i3d_feature \
 --image-feat-dim 2048 \
 --image-feat-whole-dim 32 2048 \
 --optimizer adam --adam-betas '(0.9, 0.98)' \
 --lr 0.005 --min-lr 1e-09 --lr-scheduler inverse_sqrt \
 --warmup-init-lr 1e-07 --warmup-updates 2000 \
 --max-tokens 2000 --update-freq 1 --max-update 800000 \
 --patience 10 \
 --keep-last-epochs 10 \
 --num-workers 2 \
 --log-interval 20 \
 --reset-optimizer \
 --SA-image-dropout 0.1 \
 --SA_attention_dropout 0.1

### 4. テストデータの翻訳

学習済みモデルを用いて、日本語の字幕を英語に翻訳してみましょう。

マルチモーダル機械翻訳を行うためにVISAの2000文のテストデータを準備しています。
以下のセルを実行し、テストデータを確認しましょう。

以下のコマンドを実行し、訓練済みのモデルでテストデータを翻訳してみましょう。

In [ ]:
!fairseq-generate data-bin/opvi.ja-en \
  -s ja -t en \
  --path /data/nlp/multimodal/mmt/fairseq_mmt_AI/checkpoints/opvi-ja2en/i3d/i3d-mask0/last10.ensemble.pt \
  --gen-subset test \
  --batch-size 400 --beam 5 --lenpen 0.8 \
  --quiet --remove-bpe \
  --task image_mmt \
  --image-feat-path /data/nlp/multimodal/mmt/data/VISA_i3d_feature --image-feat-dim 2048 \
  --output $model_dir/hypo.txt

!python3 rerank.py /data/nlp/multimodal/mmt/fairseq_mmt_AI/checkpoints/opvi-ja2en/i3d/i3d-mask0/hypo.txt \
 /data/nlp/multimodal/mmt/fairseq_mmt_AI/checkpoints/opvi-ja2en/i3d/i3d-mask0/hypo.sorted

!python3 meteor.py $hypo $ref

テストデータと翻訳結果の一部を確認しましょう。

In [ ]:
# 映像のディスプレイ
from IPython.display import Video
Video('/data/nlp/fairseq/TED_st/en-ja/data/train/wav/17995_0000990-0008535.wav')

# 正解データの最初の3文（日本語）
!head -n 3 /data/nlp/fairseq/TED_st/en-ja/data/test/txt/test.en

# 正解データの最初の3文（英語翻訳）
!head -n 3 /data/nlp/fairseq/TED_st/en-ja/data/test/txt/test.ja

In [ ]:
# 翻訳結果の最初の3つを表示します
!head -n 3 mt/st_outputs/test.hyp 

### 5. 自動評価

最後に、BLEU スコアでモデルを定量評価します。

In [ ]:
# JUMAN++によるセグメンテーション
!sed 's/ //g' mt/st_outputs/test.hyp | jumanpp --segment > mt/st_outputs/test.hyp.seg
!sed 's/ //g' /data/nlp/fairseq/TED_st/en-ja/data/test/txt/test.ja | jumanpp --segment > mt/st_outputs/test.ref.seg

# BLEUスコアによる評価
!fairseq-score -s mt/st_outputs/test.hyp.seg -r mt/st_outputs/test.ref.seg